# Exam Project Notebook

### Authors: 
### Bjørn Bremholm
### Laura Zeeper
### Christoffer Gade

In [317]:
# Import Packages 

import numpy as np 
import pandas as pd
import requests
import re
from bs4 import BeautifulSoup
import tweepy
import webbrowser
import time

# Suppress warning
from urllib3.exceptions import InsecureRequestWarning
requests.packages.urllib3.disable_warnings(category=InsecureRequestWarning)

# Text analysis
import nltk # NLTK: A basic, popular NLP package. 


# Header to be used in request (contact info)
header = {'Contact' : 'Christofferfoldager@gmail.com'}

## 1. Section - Gather list of twitter accounts 

Description: In this section we will collect a dataframe containing infomation of danish MPs including their twitter accounts...

Websites: 
1. https://www.ft.dk/da/medlemmer/mandatfordelingen - used to collect parties and the official MP's of each party
2. https://filip.sdu.dk/twitter/politikere/ - used to collect the twitter accounts for each MP



In [335]:
# Collect the address link of each party
url = 'https://www.ft.dk/da/medlemmer/mandatfordelingen'

header['Info'] = 'Collecting a list of MP for research project'
page = requests.get(url, verify=False, headers=header)
soup = BeautifulSoup(page.text, 'html.parser')

# Get the links
data = soup.find_all('table')[0]
aref = data.find_all('a')
member_nr = data.find_all('div', {'class':'member-container'})

# Create a list with all relevant infomation 
Parties = []

# defining red and blue 
Red = ['Socialdemokratiet (S)','Socialistisk Folkeparti (SF)','Radikale Venstre (RV)','Enhedslisten (EL)','Alternativet (ALT)']
Blue = ['Det Konservative Folkeparti (KF)', 'Venstre (V)', 'Dansk Folkeparti (DF)', 'Det Konservative Folkeparti (KF)', 'Liberal Alliance (LA)', 'Nye Borgerlige (NB)', 'Kristendemokraterne (KD)']

for i in range(len(aref)):
    if aref[i].text in Red:
        Color = 'Red'
    elif aref[i].text in Blue:
        Color = 'Blue'
    else:
        Color = None
    Parties.append([aref[i].text,Color, aref[i].get('href'),member_nr[i].text])

# Creates a Dataframe    
df_Parties = pd.DataFrame(Parties, columns=['Party','Color','AddressLink','Members'])
df_Parties.head(5)

Party Color  \
0         Socialdemokratiet (S)   Red   
1                   Venstre (V)  Blue   
2         Dansk Folkeparti (DF)  Blue   
3  Socialistisk Folkeparti (SF)   Red   
4         Radikale Venstre (RV)   Red   

                                         AddressLink Members  
0  /searchResults.aspx?sortedDescending=false&par...      49  
1  /searchResults.aspx?sortedDescending=false&par...      39  
2  /searchResults.aspx?sortedDescending=false&par...      16  
3  /searchResults.aspx?sortedDescending=false&par...      15  
4  /searchResults.aspx?sortedDescending=false&par...      14

In [343]:
# Collect the names of each MP 
ID_list = []

for i in range(len(df_Parties)): # Loop for each party
    Party = df_Parties['Party'][i]
    Color = df_Parties['Color'][i]

    #Get the relevant party page
    link = df_Parties['AddressLink'][i]
    url = f'http://ft.dk{link}&page=1&sortedBy=&pageSize=50'
    # time.sleep(1)
    page = requests.get(url, verify=False, headers=header)
    soup = BeautifulSoup(page.text, 'html.parser')

    # Get the names 
    tables = soup.find_all('tr',{'tabindex':0})

    for i in range(len(tables)): # Loop for each member of the given party 
        FirstName = tables[i].find_all('td')[1].text
        LastName = tables[i].find_all('a')[0].text
        Name = FirstName + ' ' + LastName
        MP = tables[i].find_all('td')[4].text

        # Create a first, last and middle name (for use in merge)
        Name_list = re.findall('\w+',Name)
        First_Name = Name_list[0]
        Last_Name = Name_list[-1]
        Middel_Name = ' '.join(Name_list[1:-1])

        ID_list.append([Name,Party,Color,MP,First_Name,Last_Name,Middel_Name])

df_Name = pd.DataFrame(ID_list, columns=['Name','Party','Color','MP','First Name','Last Name','Middel Name'])

# Give color to the people out of party
Red_Name = ['Susanne Zimmer','Sikandar Siddique','Uffe Elbæk'] 
Blue_Name = ['Simon Emil Ammitzbøll-Bille', 'Lars Løkke Rasmussen', 'Orla Østerby', 'Inger Støjberg']

df_Name['Color'] = np.where((df_Name['Name'].isin(Red_Name)),'Red',df_Name['Color'])
df_Name['Color'] = np.where((df_Name['Name'].isin(Blue_Name)),'Blue',df_Name['Color'])

df_Name.head()

Name                  Party Color                     MP  \
0          Ida Auken  Socialdemokratiet (S)   Red  Medlem af Folketinget   
1      Trine Bramsen  Socialdemokratiet (S)   Red  Medlem af Folketinget   
2  Bjørn Brandenborg  Socialdemokratiet (S)   Red  Medlem af Folketinget   
3        Jeppe Bruus  Socialdemokratiet (S)   Red  Medlem af Folketinget   
4     Morten Bødskov  Socialdemokratiet (S)   Red  Medlem af Folketinget   

  First Name    Last Name Middel Name  
0        Ida        Auken              
1      Trine      Bramsen              
2      Bjørn  Brandenborg              
3      Jeppe        Bruus              
4     Morten      Bødskov

In [344]:
# Collect the twitter accounts 
url = 'https://filip.sdu.dk/twitter/politikere/'
page = requests.get(url)
soup = BeautifulSoup(page.text, 'html.parser')

data = soup.find_all('div', {'class':'col-md-6 show_tweet show_user'}) # Finds the list of all politicians twitter account

Twitter_list = []

for i in range(len(data)):
    info_i = data[i].find_all('div', {'class':'media-body'})
    twitter_id = info_i[0].find('h3').text.split()
    person_id = info_i[0].find('small').text.split(' \nmed ')

    Name = person_id[0]
    Tag = twitter_id[1]
    Følgere = re.search('[0-9.]+[0-9]|\d', person_id[1]).group()

    # Create a first, last and middle name (for merge purpose)
    Name_list = re.findall('\w+',Name)
    First_Name = Name_list[0]
    Last_Name = Name_list[-1]
    Middel_Name = ' '.join(Name_list[1:-1])

    Twitter_list.append([Name,Tag,Følgere, First_Name, Last_Name,Middel_Name])

df_Twitter_id = pd.DataFrame(Twitter_list, columns=['Name','Twitter_id','Følgere','First Name','Last Name','Middel Name'])
df_Twitter_id.head(5)

Name        Twitter_id  Følgere First Name  Last Name  \
0    Margrethe Vestager         @vestager  295.359  Margrethe   Vestager   
1  Lars Løkke Rasmussen       @larsloekke  198.367       Lars  Rasmussen   
2      Pernille Skipper       @PSkipperEL   82.902   Pernille    Skipper   
3             Ida Auken         @IdaAuken   73.928        Ida      Auken   
4       Kristian Jensen  @Kristian_Jensen   62.954   Kristian     Jensen   

  Middel Name  
0              
1       Løkke  
2              
3              
4

In [345]:
# First merge effort
def merge_df(df_name,df_twitter):
    # Merge on first and last name 
    df_new = pd.merge(df_name,df_twitter[['First Name', 'Last Name','Twitter_id','Følgere']],  how='left', on=['First Name','Last Name'])
    # Merge on first and middel name
    df_new1 = pd.merge(df_name, df_twitter[['First Name', 'Last Name','Twitter_id','Følgere']],  how='left', left_on = ['First Name','Middel Name'], right_on=['First Name', 'Last Name'])

    df_new['Twitter_id'] = df_new['Twitter_id'].fillna(df_new1['Twitter_id'])
    df_new['Følgere'] = df_new['Følgere'].fillna(df_new1['Følgere'])

    # We will still miss a few Twitter_id (human error or no twitter account)
    df_new.replace(float('NaN'),'None',inplace=True)

    return df_new

df_info = merge_df(df_Name,df_Twitter_id)
twitter_missing = len(df_info.loc[df_info['Twitter_id'] == 'None'])
print ('We are missing: '+ str(twitter_missing) + ' twitter accounts')


We are missing: 32 twitter accounts


In [121]:
manuel_handles = {'Kaare Dybvad Bek':'@KaareDybvad', 'Karin Gaardsted' : '@KarinGaardsted', 'Ane Halsboe-Jørgensen':'@AneHalsboe', 
                    'Christian Rabjerg Madsen' : '@RabjergMadsen', 'Lars Aslan Rasmussen':'@lars_aslan', 'Pernille Rosenkrantz-Theil' : '@RosenkrantzT',
                    'Kasper Roug':'@KasperRoug', 'Mads  Fuglede':'@madsfuglede', 'Peter Juel-Jensen':'@PeterJuelJensen',
                    'Stén Knuth':'@Sten_Knuth',  'Lars Christian Lilleholt':'@larsclilleholt', 'Kristian Pihl Lorentzen':'@kplorentzen',
                    'Torsten Schack Pedersen':'@Torstenschack', 'Lise Bech':'@LiseBech', 'Jens Henrik Thulesen Dahl':'@JThulesen', 
                    'Mette Hjermind Dencker':'@dfmehd_mette', 'Kirsten Normann Andersen':'@KirstenNormann', 'Karina Lorentzen Dehnhardt':'@MF_K_Lorentzen',
                    'Charlotte Broman Mølbæk':'@charlottebroman', 'Rasmus Nordqvist':'@rasmusnordqvist', 'Trine Torp':'@TrineTorp', 
                    'Sofie Carsten Nielsen':'@sofiecn', 'Rasmus Helveg Petersen':'@rasmushelveg', 'Victoria Velasquez':'@VictoriaV_EL', 
                    'Katarina Ammitzbøll':'@Ammitzboell_K', 'Brigitte Klintskov Jerkel':'@JerkelK', 'Aki-Matilda Høegh-Dam': '@AkiMati_Siumut',
                    'Sjúrður Skaale': '@SjurSkaale', 'Uffe Elbæk':'@uffeelbaek'}

In [346]:
for key in manuel_handles:
    index = df_info[df_info['Name'] == key].index
    df_info.iloc[index[0],7] = manuel_handles[key]

twitter_missing = len(df_info.loc[df_info['Twitter_id'] == 'None'])
print ('We are missing: '+ str(twitter_missing) + ' twitter accounts')
df_info.head()

We are missing: 16 twitter accounts


Name                  Party Color                     MP  \
0          Ida Auken  Socialdemokratiet (S)   Red  Medlem af Folketinget   
1      Trine Bramsen  Socialdemokratiet (S)   Red  Medlem af Folketinget   
2  Bjørn Brandenborg  Socialdemokratiet (S)   Red  Medlem af Folketinget   
3        Jeppe Bruus  Socialdemokratiet (S)   Red  Medlem af Folketinget   
4     Morten Bødskov  Socialdemokratiet (S)   Red  Medlem af Folketinget   

  First Name    Last Name Middel Name      Twitter_id Følgere  
0        Ida        Auken                   @IdaAuken  73.928  
1      Trine      Bramsen               @Trinebramsen  13.517  
2      Bjørn  Brandenborg              @BjBrandenborg   2.278  
3      Jeppe        Bruus                 @JeppeBruus   4.069  
4     Morten      Bødskov                   @mfMorten  15.328

In [348]:
df_data = df_info.copy()

# Dropping columns
Columns = ['First Name', 'Last Name','Middel Name']
df_data = df_data.drop(columns=Columns, axis=1)

# Dropping those without twitter_id
df_data = df_data[df_data.Twitter_id != 'None']

# Dropping MPs from greenland and faroe islands
df_data = df_data[df_data.Color != 'None']

# Reindex
df_data = df_data.reset_index(drop=True)

# Create y binary
df_data['y'] = np.where((df_data['Color'] == 'Blue'),1,0)

# pd.set_option('display.max_rows', None)
df_data.head()


Name                  Party Color                     MP  \
0          Ida Auken  Socialdemokratiet (S)   Red  Medlem af Folketinget   
1      Trine Bramsen  Socialdemokratiet (S)   Red  Medlem af Folketinget   
2  Bjørn Brandenborg  Socialdemokratiet (S)   Red  Medlem af Folketinget   
3        Jeppe Bruus  Socialdemokratiet (S)   Red  Medlem af Folketinget   
4     Morten Bødskov  Socialdemokratiet (S)   Red  Medlem af Folketinget   

       Twitter_id Følgere  y  
0       @IdaAuken  73.928  0  
1   @Trinebramsen  13.517  0  
2  @BjBrandenborg   2.278  0  
3     @JeppeBruus   4.069  0  
4       @mfMorten  15.328  0

## Section 2 - Collecting Tweets


In [133]:
# Get authentication by twitter and access to their API 

callback_url = 'oob'
auth = tweepy.OAuthHandler(consumer_key, consumer_secret, callback_url)

try:
    redirect_url = auth.get_authorization_url()
except tweepy.TweepError:
    print('Error! Failed to get request token.')

webbrowser.open(redirect_url)

user_pin_input = input('What is the pin value? ')
auth.get_access_token(user_pin_input)
api = tweepy.API(auth)

In [324]:
# Function gathering the tweets from a specific user/handle
def extract_tweets(handle,name):

    # Input: Handle/user (e.g. @JeppeKofod) which is used to collect tweets
    #
    # Output: Dataframe containing tweets with attaching information 

    # tweets = api.user_timeline(screen_name=handle,count=40,exclude_replies=True,include_rts=False,tweet_mode="extended") 
    tweets = tweepy.Cursor(api.user_timeline,screen_name = handle, tweet_mode='extended', include_rts=False, exclude_replies=True).items()
    tweets_data = []

    for tweet in tweets:
        date = tweet.created_at
        author = tweet.author.screen_name
        likes = tweet.favorite_count
        retweets = tweet.retweet_count
        source = tweet.source
        text = tweet.full_text
        lang = tweet.lang

        tweets_data.append([date,author,name,text,lang,likes,retweets,source])

    df_tweets = pd.DataFrame(tweets_data, columns=['Date','Author','Name','Tweet','Language','Likes','Retweets','Source'])
    return df_tweets 

# Get dataframe of tweets and updated df_data
def get_tweets_df(df):
    
    df = df.reset_index(drop=True)

    df_out = pd.DataFrame()
    tweet_count = []

    for i in range(len(df)):
        
        # Find user
        user = df['Twitter_id'][i]
        name = df['Name'][i]
        
        # Collects tweets from user
        df_tweets = extract_tweets(user,name)
        df_out = df_out.append(df_tweets)

        # Collect total of tweets
        tweet_count.append(len(df_tweets))
        
        # Request limit time sleeper
        time.sleep(90)
    
    df_out = df_out.reset_index(drop=True)
    df['Tweet Count'] = tweet_count

    return df_out,df


In [340]:
########################
dont fucking run this
######################
df1 = df_data.copy()

# Get twitter data
df_twitter_data, df_Name_list = get_tweets_df(df1)

# Savinging
df_Name_list.to_csv('Name_id_list.csv')
df_twitter_data.to_csv('twitter_data.csv')

# Print
df_twitter_data.head(20)

SyntaxError: invalid syntax (<ipython-input-340-0f6344b62595>, line 2)

## 3. Procession text data

In [351]:

def preprocess(text):
    # lemmas = text.lower()
    text = re.sub('https:[\s\S]*$','', text) # remove links
    text = re.sub(r'[^\w\#\s]','', text) # should we leave hashtag or not

    tokens = nltk.TweetTokenizer().tokenize(text.lower())

    # tokens = nltk.word_tokenize(text.lower())
    # wnl = nltk.WordNetLemmatizer()
    # lemmas = [wnl.lemmatize(t) for t in tokens]

    stop_words_list = nltk.corpus.stopwords.words("danish")
    lemmas = [i for i in tokens if i not in stop_words_list]

    return lemmas # return a list of stems/lemmas


def process_tweets_text(df):

    tweet_process = []


    for i in range(len(df['Tweet'])):
        text = df['Tweet'][i]

        tweet_process.append([df['Date'][i],df['Name'][i],preprocess(text),df['Language'][i]])

    df_out = pd.DataFrame(tweet_process, columns=['Date','Name','Tweet Processed','Language'])
    
    return df_out



print(text)
print(preprocess(text))


Svært ikke at være åbenhjertig ovor for så skøn en samtalepartner som Flemming Møldrup. Lyt med her #dkpol #dkgreen #stress @Heartbeatsdk @fmpldrup https://t.co/kjvSlhyyVY
['svært', 'åbenhjertig', 'ovor', 'så', 'skøn', 'samtalepartner', 'flemming', 'møldrup', 'lyt', '#dkpol', '#dkgreen', '#stress', 'heartbeatsdk', 'fmpldrup']


In [ ]:
# Process tweets
df_tweet_processed = process_tweets_text(df_twitter_data)

# Saving the dataframes
df_tweet_processed.to_csv('Twitter_Processed.csv')

In [352]:
df_tweet_processed = process_tweets_text(df_twitter_data)
# df_twitter_data
df_tweet_processed

Date                         Name  \
0     2021-04-09 10:50:03        Niels Flemming Hansen   
1     2021-03-26 05:55:05        Niels Flemming Hansen   
2     2021-03-16 07:57:22        Niels Flemming Hansen   
3     2021-02-03 06:41:01        Niels Flemming Hansen   
4     2021-01-27 11:58:31        Niels Flemming Hansen   
5     2020-09-28 15:34:55        Niels Flemming Hansen   
6     2020-09-24 14:43:49        Niels Flemming Hansen   
7     2020-03-17 05:55:27        Niels Flemming Hansen   
8     2020-01-14 05:47:28        Niels Flemming Hansen   
9     2019-10-01 10:17:33        Niels Flemming Hansen   
10    2019-09-07 08:37:19        Niels Flemming Hansen   
11    2019-08-21 18:52:33        Niels Flemming Hansen   
12    2019-07-28 15:37:00        Niels Flemming Hansen   
13    2019-05-08 04:41:39        Niels Flemming Hansen   
14    2018-11-21 13:11:51        Niels Flemming Hansen   
15    2018-11-05 15:13:35        Niels Flemming Hansen   
16    2018-11-04 17:23:12        Niels Flemming Hansen   
17    2018-10-27 08:01:58        Niels Flemming Hansen   
18    2018-04-25 14:27:34        Niels Flemming Hansen   
19    2018-04-05 14:57:10        Niels Flemming Hansen   
20    2018-03-04 10:44:19        Niels Flemming Hansen   
21    2018-02-26 14:03:40        Niels Flemming Hansen   
22    2018-01-13 10:08:30        Niels Flemming Hansen   
23    2016-09-26 19:42:00        Niels Flemming Hansen   
24    2016-09-25 07:20:58        Niels Flemming Hansen   
25    2014-06-11 20:59:21        Niels Flemming Hansen   
26    2014-03-26 18:52:27        Niels Flemming Hansen   
27    2013-11-11 18:37:33        Niels Flemming Hansen   
28    2012-11-28 05:57:28        Niels Flemming Hansen   
29    2021-08-16 19:50:49                Rasmus Jarlov   
30    2021-08-15 13:14:28                Rasmus Jarlov   
31    2021-08-14 22:01:36                Rasmus Jarlov   
32    2021-08-13 15:53:46                Rasmus Jarlov   
33    2021-08-13 15:26:53                Rasmus Jarlov   
34    2021-08-13 10:44:37                Rasmus Jarlov   
35    2021-08-12 09:51:38                Rasmus Jarlov   
36    2021-08-11 21:01:23                Rasmus Jarlov   
37    2021-08-11 11:33:21                Rasmus Jarlov   
38    2021-08-11 09:01:32                Rasmus Jarlov   
39    2021-08-10 18:22:22                Rasmus Jarlov   
40    2021-08-10 15:08:58                Rasmus Jarlov   
41    2021-08-09 12:52:59                Rasmus Jarlov   
42    2021-08-08 11:19:09                Rasmus Jarlov   
43    2021-08-08 09:59:42                Rasmus Jarlov   
44    2021-08-07 15:07:51                Rasmus Jarlov   
45    2021-08-07 13:52:14                Rasmus Jarlov   
46    2021-08-06 13:24:22                Rasmus Jarlov   
47    2021-08-05 11:05:31                Rasmus Jarlov   
48    2021-08-04 12:39:56                Rasmus Jarlov   
49    2021-08-04 12:12:10                Rasmus Jarlov   
50    2021-08-02 14:45:25                Rasmus Jarlov   
51    2021-08-02 12:36:16                Rasmus Jarlov   
52    2021-08-02 06:52:18                Rasmus Jarlov   
53    2021-08-01 14:49:46                Rasmus Jarlov   
54    2021-08-01 09:20:30                Rasmus Jarlov   
55    2021-07-30 16:48:38                Rasmus Jarlov   
56    2021-07-29 23:23:19                Rasmus Jarlov   
57    2021-07-29 17:27:55                Rasmus Jarlov   
58    2021-07-28 22:20:18                Rasmus Jarlov   
59    2021-07-28 14:37:43                Rasmus Jarlov   
60    2021-07-27 19:00:48                Rasmus Jarlov   
61    2021-07-27 10:05:21                Rasmus Jarlov   
62    2021-07-26 20:11:22                Rasmus Jarlov   
63    2021-07-26 07:37:14                Rasmus Jarlov   
64    2021-07-23 14:28:38                Rasmus Jarlov   
65    2021-07-23 10:18:38                Rasmus Jarlov   
66    2021-07-22 20:11:55                Rasmus Jarlov   
67    2021-07-21 18:58:08                Rasmus Jarlov   
68    2021-07-21 11

In [355]:
df_tweet_processed['Tweet Processed'][0]

['våd',
 'drøm',
 'tørskoet',
 'forbindelse',
 'regeringen',
 'endelig',
 'forstået',
 'vigtigheden',
 'alsfyn',
 'forbindelse',
 'konservative',
 'samarbejde',
 'v',
 'kæmpet',
 'år',
 '#dkpol']